### Decision Tree Classifier

Now in this assignment we will be implementing the Decision Classifier for both Continuous and Categorical attributes.

Decision tree can be built by using any of the following split criterias, namely:
 - Information Gain
 - Gini Index
 - CART 

However, you are required here to implement the decision tree with information gain as splitting criterion.

Remember in my code i am not looking for maximizing the information gain, instead i am looking for minimizing the split entropy. Recall,
$$Information Gain  = H(D) - H(D_Y,D_N)$$

Where,

$H(D)$ is the data set entroy and $H(D_Y,D_N)$ is split entropy. Since $H(D)$ is constant for the given dataset so maximizing the entropy is equal to minimizing the split entropy and that is what is being represented in my code outputs.

In [81]:
%pylab inline
import scipy.stats
from collections import defaultdict  # default dictionary 
from collections import Counter

%pylab is deprecated, use %matplotlib inline and import the required libraries.
Populating the interactive namespace from numpy and matplotlib


C:\ProgramData\anaconda3\Lib\site-packages\IPython\core\magics\pylab.py:162: UserWarning: pylab import has clobbered these variables: ['split']
`%matplotlib` prevents importing * from pylab and numpy
  warn("pylab import has clobbered these variables: %s"  % clobbered +


In [2]:
#Cutomize the Matplotlib for beautiful plots...
# import dmStyle
# dmStyle.customize_mpl()
np.random.choice(100, 50, replace=True)

array([99, 74, 13, 13, 23, 12, 74, 83, 49,  5,  5, 57, 72,  4, 76, 36, 55,
       55, 99, 94, 81, 62, 42, 35, 20, 48, 70,  9, 15, 40, 33, 85, 81, 66,
       49, 49,  3, 54, 73, 43, 19, 88, 66,  6,  7, 72, 28,  1,  1,  9])

In [3]:
import pandas as pd
import tools as t # set of tools for plotting, data splitting, etc..

In [1]:
def getSplits(categories):
    '''
        function returns list of splits for the given list of categorical variables...
        
        Input:
        ------------
            categories: a list of unique categories...
        
        Return:
        ------------
            list of splits(tuples) for given list of categorical variables. Each pair of sublists
            defines the left and right splits, e.g. This list
            [('y', 'f'), ('s', 'g'), ('f'), ('y', 's', 'g')]
            
            defines two splits with each pair representing a different split.
        Examples:
        ------------
        splits=getSplits(['a1','a2','a3','a4']) will return 
        [('a1', 'a2', 'a4'), ('a3',), ('a2', 'a4'), 
        ('a1', 'a3'), ('a1', 'a4'), ('a3', 'a2'), ('a1', 'a3', 'a2'), 
        ('a4',), ('a3', 'a4'), ('a1', 'a2'), ('a1',), ('a3', 'a2', 'a4'), ('a2',), ('a1', 'a3', 'a4')]

            
    '''
    categories=set(categories)
    tsplits=t.get_powerset(categories,len(categories)-1) # get all the power sets with the given cardinality...
    flist=[]
    for s in tsplits:

        if not s in flist:
            r=categories.difference(s)
    #         print s, tuple(r)
            flist.append(s)
            flist.append(r)

    olist=[]

    for s in flist:
        ilist=[]

        for k in s:
            ilist.append(k)
        olist.append(tuple(ilist))

#     print olist
    
    return olist

In [2]:
def compute_entropy(counts):
    """
    Compute entropy given class counts.
    """
    total = sum(counts)
    entropy = 0.0
    for count in counts:
        if count > 0:
            probability = count / total
            entropy -= probability * math.log2(probability)
    return entropy

In [3]:
splits=getSplits(['a1','a2','a3','a4'])
print (splits,len(splits))

NameError: name 't' is not defined

In [110]:
class Node:
    def __init__(self,purity,klasslabel='',score=0,split=[],fidx=-1):
        '''
            purity: purity level at which to stop
            klasslabel: klasslabel of the node, (for leaf node)
            score: information gain of the newly added node
            split: splitting threshold
            fidx: feature index            
        '''
        self.lchild=None
        self.rchild=None
        self.klasslabel=klasslabel        
        self.split=split
        self.score=score
        self.fidx=fidx
        self.purity=purity
        self.ftype= 'categorical' if type(self.split) in [tuple, str, numpy.string_] else 'continuous' # feature type 

        
    def set_childs(self,lchild,rchild):
        self.lchild=lchild       
        self.rchild=rchild

    def isleaf(self):
        if self.lchild==None and self.rchild==None:
            return True
        return False
    
    def isless_than_eq(self, X):
        """
        Check if the feature value in X at index fidx satisfies the split condition.
        For numerical splits, check `<= split`; for categorical splits, check `in split`.
        """
        # Numeric split case
        if isinstance(self.split, (int, float)):
            return X[self.fidx] <= self.split
        
        # Categorical split case (assuming self.split is a set of categories)
        elif isinstance(self.split, set):
            return X[self.fidx] in self.split
        
    def get_str(self):        
        if self.isleaf():
            return 'C(class={},Purity={})'.format(self.klasslabel,self.purity)
        else:
            return 'I(Fidx={},Score={},Split={})'.format(self.fidx,self.score,self.split)
    

In [51]:
def is_categorical(feat):
    """
    Determines if a feature is categorical based on its data type or unique values.
    """
    # Option 1: Check if the data type is object (for pandas or numpy arrays)
    if feat.dtype == 'object' or feat.dtype == np.str_:
        return True

    # Option 2: Check if there are fewer unique values than a threshold
    # This is useful if you have numeric categorical features like [1, 2, 3].
    unique_values = np.unique(feat)
    if len(unique_values) < 10:  # arbitrary threshold for small unique values
        return True
    
    return False


In [161]:
### import pdb
## Your code goes here...
# You might need to define auxliary classes for composition.. ?
class DecisionTree:
    ''' Implements the Decision Tree For Classification... '''
    def __init__(self, purityp, exthreshold, maxdepth=10):        
        self.purity = purityp
        self.exthreshold = exthreshold
        self.maxdepth = maxdepth
        
        
    def train(self, X, Y):
        ''' Train Decision Tree using the given 
            X [m x d] data matrix and Y labels matrix
            
            Input:
            ------
            X: [m x d] a data matrix of m d-dimensional examples.
            Y: [m x 1] a label vector.
            
            Returns:
            -----------
            Nothing
            '''
        nexamples, nfeatures = X.shape
        self.klasses=np.unique(Y)
        self.tree = self.build_tree(X, Y, depth=0)        


    def evaluate_categorical_attribute(self, feat, Y):
        """
        Evaluates the categorical attribute for all possible split points, 
        i.e., 2^(m-1)-2 possible feature selections.

        Input:
        ---------
        feat: a categorical feature (array of categorical values)
        Y: labels (array of corresponding labels)

        Returns:
        ----------
        v: splitting threshold (the best split point)
        score: splitting score (the minimum entropy)
        Xlidx: Index of examples belonging to the left child node
        Xridx: Index of examples belonging to the right child node
        """
        categories = set(feat)
        splits = getSplits(categories) if len(categories) > 1 else [categories]

        feat = np.array(feat)
        Y = np.array(Y)

        # Frequency of each class in the entire set
        unique_classes, total_counts = np.unique(Y, return_counts=True)
        total_entropy = compute_entropy(total_counts)
        
        # Initialize best split metrics
        mingain = float('-inf')
        best_split = None
        Xlidx, Xridx = None, None

        for split in splits:
            # Partition indices based on the split
            left_indices = [i for i, val in enumerate(feat) if val in split]
            right_indices = [i for i, val in enumerate(feat) if val not in split]
            
            # Count classes in each partition
            left_counts = np.unique(Y[left_indices], return_counts=True)[1]
            right_counts = np.unique(Y[right_indices], return_counts=True)[1]

            # Compute weighted entropy for the split
            left_weight = len(left_indices) / len(Y)
            right_weight = len(right_indices) / len(Y)
            split_entropy = left_weight * compute_entropy(left_counts) + right_weight * compute_entropy(right_counts)

            # Compute information gain
            gain = total_entropy - split_entropy

            # Update best split if current gain is higher
            if gain > mingain:
                mingain = gain
                best_split = split
                Xlidx = left_indices
                Xridx = right_indices

        return best_split, mingain, Xlidx, Xridx
        
    def evaluate_numerical_attribute(self, feat, Y):
        '''
        Evaluates the numerical attribute for all possible split points for
        possible feature selection. Handles any number of classes.

        Input:
        ---------
        feat: a continuous feature (numpy array)
        Y: labels (numpy array)

        Returns:
        ----------
        v: splitting threshold
        score: splitting score (minimum entropy)
        Xlidx: Index of examples belonging to left child node
        Xridx: Index of examples belonging to right child node
        '''
        best_score = float('inf')  # We want to minimize entropy
        best_split = None
        Xlidx, Xridx = None, None

        # Sort features and corresponding labels
        sidx = np.argsort(feat)
        f = feat[sidx]  # sorted features
        sY = Y[sidx]    # sorted labels

        # Get unique class labels and their counts
        unique_labels, label_counts = np.unique(sY, return_counts=True)
        n_samples = len(sY)

        # Calculate initial entropy of the entire dataset
        class_probabilities = label_counts / n_samples
        H_D = -np.sum(class_probabilities * np.log2(class_probabilities + 1e-9))

        # Find potential split points (midpoints between unique values)
        unique_vals = np.unique(f)
        possible_splits = [(unique_vals[i] + unique_vals[i + 1]) / 2 
                          for i in range(len(unique_vals) - 1)]

        for split_point in possible_splits:
            # Create masks for left and right partitions
            left_mask = f <= split_point
            right_mask = f > split_point

            # Only consider valid splits (both partitions non-empty)
            if np.any(left_mask) and np.any(right_mask):
                left_labels = sY[left_mask]
                right_labels = sY[right_mask]

                # Calculate probabilities and entropy for left partition
                left_counts = np.unique(left_labels, return_counts=True)[1]
                left_probs = left_counts / len(left_labels)
                entropy_left = -np.sum(left_probs * np.log2(left_probs + 1e-9))

                # Calculate probabilities and entropy for right partition
                right_counts = np.unique(right_labels, return_counts=True)[1]
                right_probs = right_counts / len(right_labels)
                entropy_right = -np.sum(right_probs * np.log2(right_probs + 1e-9))

                # Calculate weighted average entropy for this split
                left_weight = len(left_labels) / n_samples
                right_weight = len(right_labels) / n_samples
                split_entropy = (left_weight * entropy_left) + (right_weight * entropy_right)

                # Update best split if current entropy is lower
                if split_entropy < best_score:
                    best_score = split_entropy
                    best_split = split_point
                    Xlidx = sidx[left_mask]  # Convert back to original indices
                    Xridx = sidx[right_mask]

        return best_split, best_score, Xlidx, Xridx


    def test(self, X):
        
        ''' Test the trained classifiers on the given set of examples 
        
                   
            Input:
            ------
            X: [m x d] a data matrix of m d-dimensional test examples.
           
            Returns:
            -----------
                pclass: the predicted class for each example, i.e. to which it belongs
        '''
        
        nexamples, nfeatures=X.shape
        pclasses=self.predict(X)
                
        return np.array(pclasses)
    
    def predict(self, X):
        """
        Predict the class for each example in the given data matrix X.
        
        Parameters:
        -----------
        X : numpy.ndarray
            [m x d] data matrix of m d-dimensional test examples.
        
        Returns:
        --------
        list
            Predicted classes for each example in X.
        """
        
        pclasses = []

        for idx in range(X.shape[0]):
            pclasses.append(self._predict(self.tree, X[idx, :]))
        
        return pclasses
    
    def _predict(self, node, X):
        """
        Recursively predict the class for a single example by traversing the tree.

        Parameters:
        -----------
        node : Node
            The current node in the decision tree.
        X : numpy.ndarray
            A single test example (1 x d).

        Returns:
        --------
        int
            Predicted class for the given example.
        """
        print("Prediction for single example: ",X)
        # If the node is a leaf, return its class label
        if node.isleaf():
            print(f"i am leaf label class: {node.klasslabel}")
            return node.klasslabel

        # Traverse the tree according to the split condition
        if node.isless_than_eq(X):
            print("Going to the left")
            return self._predict(node.lchild, X)  # Go to left child
        else:
            print("Going to the right")
            return self._predict(node.rchild, X)  # Go to right child

    def calculate_purity(self, Y):
        """
        Calculates the purity of the current node based on the distribution of labels in Y.
        
        Purity here is measured by the fraction of the most common label in Y.
        """
        
        label_counts = Counter(Y) # {'Iris-setosa': 3, 'Iris-virginica': 2}
        max_label = max(label_counts.values()) # 3

        # Step 3: Calculate purity
        purity = max_label / len(Y)
        
        return purity
    def __str__(self):
        str = '---------------------------------------------------'
        str += '\n A Decision Tree With Depth={}'.format(self.find_depth())
        str += self.__print(self.tree)
        str += '\n---------------------------------------------------'
        return str  # self.__print(self.tree)        
        
     
   
    def find_depth(self):
        return self._find_depth(self.tree)
    def _find_depth(self, node):
        if not node:
            return
        if node.isleaf():
            return 1
        else:
            return max(self._find_depth(node.lchild), self._find_depth(node.rchild)) + 1
    def __print(self, node, depth=0):
        
        ret = ""

        # Print right branch
        if node.rchild:
            ret += self.__print(node.rchild, depth + 1)

        # Print own value
        
        ret += "\n" + ("    "*depth) + node.get_str()

        # Print left branch
        if node.lchild:
            ret += self.__print(node.lchild, depth + 1)
        
        return ret
    


#     def build_tree(self, X, Y, depth):
#         """
#         Recursively builds a decision tree that properly handles both categorical and numerical features.

#         Input:
#         -----
#         X: [m x d] a data matrix of m d-dimensional examples
#         Y: [m x 1] a label vector
#         depth: current depth in the tree

#         Returns:
#         -------
#         Node: root node of the built tree
#         """
#         nexamples, nfeatures = X.shape
#         klasses = np.unique(Y)
#         current_purity = self.calculate_purity(Y)

#         # Check termination conditions
#         if (len(klasses) == 1 or 
#             current_purity >= self.purity or 
#             depth >= self.maxdepth or 
#             nexamples <= self.exthreshold):

#             # Create leaf node with majority class
#             label_counts = Counter(Y)
#             majority_label = max(label_counts, key=label_counts.get)
#             leaf_purity = label_counts[majority_label] / len(Y)
#             return Node(purity=leaf_purity, klasslabel=majority_label)

#         # Initialize best split variables
#         best_feature_score = float('inf')
#         best_feature_index = None
#         best_split_value = None
#         best_left_indices = None
#         best_right_indices = None

#         # Evaluate all features to find the best split
#         for feature_idx in range(nfeatures):
#             feature_values = X[:, feature_idx]

#             if is_categorical(feature_values):
#                 # Handle categorical feature
#                 split_value, score, left_idx, right_idx = self.evaluate_categorical_attribute(
#                     feature_values, Y)

#                 # Check if this split is valid and better than current best
#                 if (split_value is not None and 
#                     left_idx is not None and 
#                     right_idx is not None and
#                     len(left_idx) > 0 and 
#                     len(right_idx) > 0 and 
#                     score < best_feature_score):

#                     best_feature_score = score
#                     best_feature_index = feature_idx
#                     best_split_value = split_value
#                     best_left_indices = left_idx
#                     best_right_indices = right_idx
#             else:
#                 # Handle numerical feature
#                 split_value, score, left_idx, right_idx = self.evaluate_numerical_attribute(
#                     feature_values, Y)

#                 # Check if this split is valid and better than current best
#                 if (split_value is not None and 
#                     left_idx is not None and 
#                     right_idx is not None and
#                     len(left_idx) > 0 and 
#                     len(right_idx) > 0 and 
#                     score < best_feature_score):

#                     best_feature_score = score
#                     best_feature_index = feature_idx
#                     best_split_value = split_value
#                     best_left_indices = left_idx
#                     best_right_indices = right_idx

#         # If no valid split found, create a leaf node
#         if (best_feature_index is None or 
#             best_left_indices is None or 
#             best_right_indices is None or
#             len(best_left_indices) == 0 or 
#             len(best_right_indices) == 0):

#             label_counts = Counter(Y)
#             majority_label = max(label_counts, key=label_counts.get)
#             leaf_purity = label_counts[majority_label] / len(Y)
#             return Node(purity=leaf_purity, klasslabel=majority_label)

#         # Create decision node with the best split
#         node = Node(
#             purity=current_purity,
#             score=best_feature_score,
#             split=[best_split_value],
#             fidx=best_feature_index
#         )

#         # Split data and recursively build left and right subtrees
#         X_left, Y_left = X[best_left_indices], Y[best_left_indices]
#         X_right, Y_right = X[best_right_indices], Y[best_right_indices]

#         # Recursively build child nodes
#         node.set_childs(
#             self.build_tree(X_left, Y_left, depth + 1),
#             self.build_tree(X_right, Y_right, depth + 1)
#         )

#         return node

    def is_categorical(feature):
        """
        Determines if a feature is categorical.
        Returns True if the feature contains non-numeric values or
        if it contains only integers with a small number of unique values.
        """
        try:
            # Check if all values are numeric
            feature = np.array(feature)
            if not np.issubdtype(feature.dtype, np.number):
                return True

            # If numeric, check if it's categorical-like
            unique_values = np.unique(feature)
            if (np.all(np.equal(np.mod(feature, 1), 0)) and  # all integers
                len(unique_values) <= 10):  # small number of unique values
                return True

            return False
        except:
            return True  # If any error occurs, assume categorical
        
    def build_tree(self, X, Y, depth):
        """ 
            Function is used to recursively build the decision Tree 
          
            Input
            -----
            X: [m x d] a data matrix of m d-dimensional examples.
            Y: [m x 1] a label vector.
            
            Returns
            -------
            root node of the built tree...
        """
        nexamples, nfeatures=X.shape
#         print(Y)
        klasses=np.unique(Y);
#         print(f"Rows: {nexamples}, nfeatures: {nfeatures}")
#         print("Number of classes: ",len(klasses))
        current_purity = self.calculate_purity(Y)
        
        print(f"Current purity of Y: {current_purity}")
        
        # IF NUMBER OF CLASS IN A NODE IS 1 MEANING PURE LABEL
        # IF PURITY THRESHOLD IS MET >0.95
        # IF MAX DEPT IS MET IE 10
        # THE MINIMUM NUMBER OF EXAMPLE IN A NODE IS MET
        
        if len(klasses)==1 or current_purity>=self.purity or depth >= self.maxdepth or nexamples <= self.exthreshold:
            print("Pure label")
            label_counts = Counter(Y)

            # Step 1: Determine the label with the maximum count
            final_label = max(label_counts, key=label_counts.get)

            # Step 2: Calculate purity as the maximum count divided by total examples
            max_count = label_counts[final_label]
            purity = max_count / len(Y)
            
            print(f"purity: {purity}, klasslabel: {final_label}")
        
            return Node(purity, klasslabel=final_label)
            
        print("leaf node is not decided yet")
        
        Node_best_score = float('-inf')  # We want to minimize entropy
        Node_best_split = None
        Node_Xlidx, Node_Xridx = None, None
        feature_index=None
        
        # GETTING THE BEST SPLIT POINT
        
        for i in range(nfeatures):
            print(f"Number of row: {len(X[:,i])}")
            
            if is_categorical(X[:,i]):
                print("categoric is called")
                best_split, best_score, Xlidx, Xridx = self.evaluate_categorical_attribute(X[:,i],Y)
            else:
                print("Numeric is called")
                # Call the evaluate_numeric_attribute function
                best_split, best_score, Xlidx, Xridx = self.evaluate_numeric_attribute(X[:,i],Y)

            #print(best_split, best_score, Xlidx, Xridx)
            
            if best_score> Node_best_score:
                print(f"Best feature: {i}")
                feature_index=i
                Node_best_split = best_split
                Node_best_score = best_score
                Node_Xlidx, Node_Xridx = Xlidx, Xridx
          
        """
            def __init__(self,purity,klasslabel='',score=0,split=[],fidx=-1):
            self.lchild=None       
            self.rchild=None
            self.klasslabel=klasslabel        
            self.split=split
            self.score=score
            self.fidx=fidx #feature index
            self.purity=purity
        """
        print(f"The best root node is\n Best feature index: {feature_index}\n",Node_best_split, Node_best_score,"\n")
        
        # If no valid split, return a leaf node
        if feature_index is None or Node_Xlidx is None or Node_Xridx is None or len(Node_Xlidx) == 0 or len(Node_Xridx) == 0:
             
            label_counts = Counter(Y)

            # Step 1: Determine the label with the maximum count
            final_label = max(label_counts, key=label_counts.get)

            # Step 2: Calculate purity as the maximum count divided by total examples
            max_count = label_counts[final_label]
            purity = max_count / len(Y)
        
            return Node(purity, klasslabel=final_label) # self,purity,klasslabel='',score=0,split=[],fidx=-1)
        
    
    
        print(f"A node is being created with feature index: {feature_index}")
        node = Node(purity=current_purity, score=Node_best_score, split=[Node_best_split], fidx=feature_index)

                
        """
        X_left = X[Xlidx]  # X_left = [ [1.5], [2.5], [3.0] ]
        Y_left = Y[Xlidx]  # Y_left = [ 0,     0,     1     ]

        X_right = X[Xridx] # X_right = [ [3.5], [4.5], [5.5] ]
        Y_right = Y[Xridx] # Y_right = [ 1,     1,     0     ]

        """
        
        X_left, Y_left = X[Node_Xlidx], Y[Node_Xlidx]
        X_right, Y_right = X[Node_Xridx], Y[Node_Xridx]
        
        if len(Y_left) == 0 or len(Y_right) == 0:
            label_counts = Counter(Y)

            # Step 1: Determine the label with the maximum count
            final_label = max(label_counts, key=label_counts.get)

            # Step 2: Calculate purity as the maximum count divided by total examples
            max_count = label_counts[final_label]
            purity = max_count / len(Y)
        
            return Node(purity, klasslabel=final_label)
            
            
        node.set_childs(self.build_tree(X_left, Y_left, depth + 1),
                        self.build_tree(X_right, Y_right, depth + 1))
        
        
        return node    

In [162]:
# Lets train a Decision Tree Classifier two features
feat=np.arange(2)
dt=DecisionTree(0.95,5,10)
dt.train(Xtrain[:,feat],Ytrain)

Current purity of Y: 0.51802356251099
leaf node is not decided yet
Number of row: 5687
categoric is called
Best feature: 0
Number of row: 5687
categoric is called
The best root node is
 Best feature index: 0
 ('s', 'b') 0.03259859006398591 

A node is being created with feature index: 0
Current purity of Y: 0.9031339031339032
leaf node is not decided yet
Number of row: 351
categoric is called
Best feature: 0
Number of row: 351
categoric is called
Best feature: 1
The best root node is
 Best feature index: 1
 ('g', 'y') 0.01756232776778549 

A node is being created with feature index: 1
Current purity of Y: 0.8347826086956521
leaf node is not decided yet
Number of row: 115
categoric is called
Best feature: 0
Number of row: 115
categoric is called
Best feature: 1
The best root node is
 Best feature index: 1
 ('g',) 0.02286888273353127 

A node is being created with feature index: 1
Current purity of Y: 1.0
Pure label
purity: 1.0, klasslabel: p
Current purity of Y: 0.8421052631578947
leaf 

In [152]:
pclasses=dt.predict(Xtest[:,feat])

Prediction for single example:  ['k' 's']
Going to the right
Prediction for single example:  ['k' 's']
Going to the right
Prediction for single example:  ['k' 's']
Going to the right
Prediction for single example:  ['k' 's']
Going to the right
Prediction for single example:  ['k' 's']
Going to the right
Prediction for single example:  ['k' 's']
i am leaf label class: e
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
i am leaf label class: e
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction f

Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
i am leaf label class: e
Prediction for single example:  ['f' 's']
Going to the right
Prediction for single example:  ['f' 's']
Going to the right
Prediction for single example:  ['f' 's']
Going to the right
Prediction for single example:  ['f' 's']
Going to the right
Prediction for single example:  ['f' 's']
Going to the right
Prediction for single example:  ['f' 's']
i am leaf label class: e
Prediction for single example:  ['x' 'f']
Going to the right
Prediction for single example:  ['x' 'f']
Going to the right
Prediction for single example:  ['x' 'f']
Going to the right
Prediction for single example:  ['x' 'f']
Going to the right
Prediction f

Prediction for single example:  ['x' 'f']
Going to the right
Prediction for single example:  ['x' 'f']
Going to the right
Prediction for single example:  ['x' 'f']
Going to the right
Prediction for single example:  ['x' 'f']
Going to the right
Prediction for single example:  ['x' 'f']
i am leaf label class: e
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
i am leaf label class: e
Prediction for single example:  ['f' 's']
Going to the right
Prediction for single example:  ['f' 's']
Going to the right
Prediction for single example:  ['f' 's']
Going to the right
Prediction for single example:  ['f' 's']
Going to the right
Prediction for single example:  ['f' 's']
Going to the right
Prediction f

Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
i am leaf label class: e
Prediction for single example:  ['k' 'y']
Going to the right
Prediction for single example:  ['k' 'y']
Going to the right
Prediction for single example:  ['k' 'y']
Going to the right
Prediction for single example:  ['k' 'y']
Going to the right
Prediction for single example:  ['k' 'y']
Going to the right
Prediction for single example:  ['k' 'y']
i am leaf label class: e
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
i am leaf label class: e
Prediction for single example:  ['f' 'f']
Going to the right
Predic

# Lets test our code for the given example in the book.

In [122]:
#load the Iris dataset
tdata=pd.read_csv('./iris.data')
tdata.columns=['SepalLength','SepalWidth','PetalLength','PetalWidth','Class']

In [123]:
tx=tdata['SepalLength'].dropna()
tx[(tdata['SepalLength']>=4.3) & (tdata['SepalLength']<=5.2)]='a1'
tx[(tdata['SepalLength']>5.2) & (tdata['SepalLength']<=6.1)]='a2'
tx[(tdata['SepalLength']>6.1) & (tdata['SepalLength']<=7.0)]='a3'
tx[(tdata['SepalLength']>7.0) & (tdata['SepalLength']<=7.9)]='a4'

In [124]:
print (tx.values)
Y=tdata['Class'].dropna()
Y[Y=='Iris-virginica']='Iris-versicolor'
Y=Y.values
print (Y)

['a1' 'a1' 'a1' 'a1' 'a2' 'a1' 'a1' 'a1' 'a1' 'a2' 'a1' 'a1' 'a1' 'a2'
 'a2' 'a2' 'a1' 'a2' 'a1' 'a2' 'a1' 'a1' 'a1' 'a1' 'a1' 'a1' 'a1' 'a1'
 'a1' 'a1' 'a2' 'a1' 'a2' 'a1' 'a1' 'a2' 'a1' 'a1' 'a1' 'a1' 'a1' 'a1'
 'a1' 'a1' 'a1' 'a1' 'a1' 'a2' 'a1' 'a3' 'a3' 'a3' 'a2' 'a3' 'a2' 'a3'
 'a1' 'a3' 'a1' 'a1' 'a2' 'a2' 'a2' 'a2' 'a3' 'a2' 'a2' 'a3' 'a2' 'a2'
 'a2' 'a3' 'a2' 'a3' 'a3' 'a3' 'a3' 'a2' 'a2' 'a2' 'a2' 'a2' 'a2' 'a2'
 'a2' 'a3' 'a3' 'a2' 'a2' 'a2' 'a2' 'a2' 'a1' 'a2' 'a2' 'a2' 'a3' 'a1'
 'a2' 'a3' 'a2' 'a4' 'a3' 'a3' 'a4' 'a1' 'a4' 'a3' 'a4' 'a3' 'a3' 'a3'
 'a2' 'a2' 'a3' 'a3' 'a4' 'a4' 'a2' 'a3' 'a2' 'a4' 'a3' 'a3' 'a4' 'a3'
 'a2' 'a3' 'a4' 'a4' 'a4' 'a3' 'a3' 'a2' 'a4' 'a3' 'a3' 'a2' 'a3' 'a3'
 'a3' 'a2' 'a3' 'a3' 'a3' 'a3' 'a3' 'a3' 'a2']
['Iris-setosa' 'Iris-setosa' 'Iris-setosa' 'Iris-setosa' 'Iris-setosa'
 'Iris-setosa' 'Iris-setosa' 'Iris-setosa' 'Iris-setosa' 'Iris-setosa'
 'Iris-setosa' 'Iris-setosa' 'Iris-setosa' 'Iris-setosa' 'Iris-setosa'
 'Iris-setosa' 'Iris-setosa' '

In [125]:
%pdb off
dt=DecisionTree(0.95,5,5)
dt.evaluate_categorical_attribute(tx,Y)

Automatic pdb calling has been turned OFF


(('a1',),
 0.40305408062182424,
 [0,
  1,
  2,
  3,
  5,
  6,
  7,
  8,
  10,
  11,
  12,
  16,
  18,
  20,
  21,
  22,
  23,
  24,
  25,
  26,
  27,
  28,
  29,
  31,
  33,
  34,
  36,
  37,
  38,
  39,
  40,
  41,
  42,
  43,
  44,
  45,
  46,
  48,
  56,
  58,
  59,
  92,
  97,
  105],
 [4,
  9,
  13,
  14,
  15,
  17,
  19,
  30,
  32,
  35,
  47,
  49,
  50,
  51,
  52,
  53,
  54,
  55,
  57,
  60,
  61,
  62,
  63,
  64,
  65,
  66,
  67,
  68,
  69,
  70,
  71,
  72,
  73,
  74,
  75,
  76,
  77,
  78,
  79,
  80,
  81,
  82,
  83,
  84,
  85,
  86,
  87,
  88,
  89,
  90,
  91,
  93,
  94,
  95,
  96,
  98,
  99,
  100,
  101,
  102,
  103,
  104,
  106,
  107,
  108,
  109,
  110,
  111,
  112,
  113,
  114,
  115,
  116,
  117,
  118,
  119,
  120,
  121,
  122,
  123,
  124,
  125,
  126,
  127,
  128,
  129,
  130,
  131,
  132,
  133,
  134,
  135,
  136,
  137,
  138,
  139,
  140,
  141,
  142,
  143,
  144,
  145,
  146,
  147,
  148])

In [126]:
is_categorical(tx)

True

In [127]:
from nose.tools import assert_almost_equal, assert_almost_equals

%pdb off
dt=DecisionTree(0.95,5,5)
split, gain, Xlidx, Xridx = dt.evaluate_categorical_attribute(tx,Y)


assert_almost_equal('a1', split[0])
assert_almost_equal(gain, 0.40, 1)

Automatic pdb calling has been turned OFF


# Now lets test on [Mushroom](https://archive.ics.uci.edu/ml/machine-learning-databases/mushroom/agaricus-lepiota.names) dataset


This data set includes descriptions of hypothetical samples corresponding to 23 species of gilled mushrooms in the Agaricus and Lepiota Family (pp. 500-525).  Each species is identified as definitely edible, definitely poisonous, or of unknown edibility and not recommended.  This latter class was combined with the poisonous one.  The Guide clearly states that there is no simple rule for determining the edibility of a mushroom; no rule like ``leaflets three, let it be'' for Poisonous Oak and Ivy.


- Number of Instances: 8124

- Number of Attributes: 22 (all nominally valued)

- Attribute Information: (classes: edible=e, poisonous=p)
         1. cap-shape:                bell=b,conical=c,convex=x,flat=f, knobbed=k,sunken=s
         2. cap-surface:              fibrous=f,grooves=g,scaly=y,smooth=s
         3. cap-color:                brown=n,buff=b,cinnamon=c,gray=g,green=r, pink=p,purple=u,red=e,white=w,yellow=y
         4. bruises?:                 bruises=t,no=f
         5. odor:                     almond=a,anise=l,creosote=c,fishy=y,foul=f, musty=m,none=n,pungent=p,spicy=s
         6. gill-attachment:          attached=a,descending=d,free=f,notched=n
         7. gill-spacing:             close=c,crowded=w,distant=d
         8. gill-size:                broad=b,narrow=n
         9. gill-color:               black=k,brown=n,buff=b,chocolate=h,gray=g, green=r,orange=o,pink=p,purple=u,red=e,white=w,yellow=y
        10. stalk-shape:              enlarging=e,tapering=t
        11. stalk-root:               bulbous=b,club=c,cup=u,equal=e, rhizomorphs=z,rooted=r,missing=?
        12. stalk-surface-above-ring: fibrous=f,scaly=y,silky=k,smooth=s
        13. stalk-surface-below-ring: fibrous=f,scaly=y,silky=k,smooth=s
        14. stalk-color-above-ring:   brown=n,buff=b,cinnamon=c,gray=g,orange=o, pink=p,red=e,white=w,yellow=y
        15. stalk-color-below-ring:   brown=n,buff=b,cinnamon=c,gray=g,orange=o, pink=p,red=e,white=w,yellow=y
        16. veil-type:                partial=p,universal=u
        17. veil-color:               brown=n,orange=o,white=w,yellow=y
        18. ring-number:              none=n,one=o,two=t
        19. ring-type:                cobwebby=c,evanescent=e,flaring=f,large=l, none=n,pendant=p,sheathing=s,zone=z
        20. spore-print-color:        black=k,brown=n,buff=b,chocolate=h,green=r, orange=o,purple=u,white=w,yellow=y
        21. population:               abundant=a,clustered=c,numerous=n, scattered=s,several=v,solitary=y
        22. habitat:                  grasses=g,leaves=l,meadows=m,paths=p, urban=u,waste=w,woods=d

- Missing Attribute Values: 2480 of them (denoted by "?"), all for  attribute #11.

- Class Distribution: 
        --    edible: 4208 (51.8%)
        -- poisonous: 3916 (48.2%)
        --     total: 8124 instances

In [153]:
#load the data set
data=pd.read_csv('./mushrooms.csv')
data.columns=columns=['class', 'cap-shape','cap-surface','cap-color','bruises?','odor','gill-attachment','gill-spacing','gill-size','gill-color','stalk-shape','stalk-root','stalk-surface-above-ring','stalk-surface-below-ring','stalk-color-above-ring','stalk-color-below-ring','veil-type','veil-color','ring-number','ring-type','spore-print-color','population','habitat']
print (data.describe())

       class cap-shape cap-surface cap-color bruises?  odor gill-attachment  \
count   8124      8124        8124      8124     8124  8124            8124   
unique     2         6           4        10        2     9               2   
top        e         x           y         n        f     n               f   
freq    4208      3656        3244      2284     4748  3528            7914   

       gill-spacing gill-size gill-color  ... stalk-surface-below-ring  \
count          8124      8124       8124  ...                     8124   
unique            2         2         12  ...                        4   
top               c         b          b  ...                        s   
freq           6812      5612       1728  ...                     4936   

       stalk-color-above-ring stalk-color-below-ring veil-type veil-color  \
count                    8124                   8124      8124       8124   
unique                      9                      9         1          4   
to

In [154]:
data.tail()

class cap-shape cap-surface cap-color bruises? odor gill-attachment  \
8119     e         k           s         n        f    n               a   
8120     e         x           s         n        f    n               a   
8121     e         f           s         n        f    n               a   
8122     p         k           y         n        f    y               f   
8123     e         x           s         n        f    n               a   

     gill-spacing gill-size gill-color  ... stalk-surface-below-ring  \
8119            c         b          y  ...                        s   
8120            c         b          y  ...                        s   
8121            c         b          n  ...                        s   
8122            c         n          b  ...                        k   
8123            c         b          y  ...                        s   

     stalk-color-above-ring stalk-color-below-ring veil-type veil-color  \
8119                      o                      o         p          o   
8120                      o                      o         p          n   
8121                      o                      o         p          o   
8122                      w                      w         p          w   
8123                      o                      o         p          o   

     ring-number ring-type spore-print-color population habitat  
8119           o         p                 b          c       l  
8120           o         p                 b          v       l  
8121           o         p                 b          c       l  
8122           o         e                 w          v       l  
8123           o         p                 o          c       l  

[5 rows x 23 columns]

In [155]:
# Get your data in matrix
X = np.asarray(data.iloc[:, 1:].dropna())
Y = np.asarray(data.iloc[:, 0].dropna())

print (" Data Set Dimensions=", X.shape, " True Class labels dimensions", Y.shape )  

 Data Set Dimensions= (8124, 22)  True Class labels dimensions (8124,)


In [156]:
# Split your data into training and test-set... 
# see the documentation of split_data in tools for further information...
Xtrain,Ytrain,Xtest,Ytest=t.split_data(X,Y)

print (" Training Data Set Dimensions=", Xtrain.shape, "Training True Class labels dimensions", Ytrain.shape )  
print (" Test Data Set Dimensions=", Xtest.shape, "Test True Class labels dimensions", Ytrain.shape  ) 


 Training Data Set Dimensions= (5687, 22) Training True Class labels dimensions (5687,)
 Test Data Set Dimensions= (2437, 22) Test True Class labels dimensions (5687,)


In [157]:
# Lets train a Decision Tree Classifier two features
%pdb
feat=np.arange(2)
dt=DecisionTree(0.95,5,10)
dt.train(Xtrain[:,feat],Ytrain)

Automatic pdb calling has been turned ON
Current purity of Y: 0.51802356251099
leaf node is not decided yet
5687 5687
categoric is called
Best feature: 0
5687 5687
categoric is called
The best root node is
 Best feature index: 0
 ('s', 'b') 0.03187195964713674 

A node is being created with feature index: 0
Current purity of Y: 0.9074626865671642
leaf node is not decided yet
335 335
categoric is called
Best feature: 0
335 335
categoric is called
The best root node is
 Best feature index: 0
 ('s',) 0.010433915635054802 

A node is being created with feature index: 0
Current purity of Y: 1.0
Pure label
purity: 1.0, klasslabel: e
Current purity of Y: 0.9003215434083601
leaf node is not decided yet
311 311
categoric is called
Best feature: 0
311 311
categoric is called
Best feature: 1
The best root node is
 Best feature index: 1
 ('f', 'y', 's') 0.010764553446515002 

A node is being created with feature index: 1
Current purity of Y: 0.9032258064516129
leaf node is not decided yet
310 310


In [158]:
print (dt)

---------------------------------------------------
 A Decision Tree With Depth=7
                    C(class=e,Purity=0.5072314049586777)
                I(Fidx=1,Score=0.0012749879863722668,Split=[('s',)])
                    C(class=p,Purity=0.535064935064935)
            I(Fidx=0,Score=0.0032404880549454784,Split=[('f',)])
                    C(class=p,Purity=0.5428881650380022)
                I(Fidx=1,Score=0.006151276592026633,Split=[('g', 's')])
                        C(class=p,Purity=1.0)
                    I(Fidx=1,Score=0.0011568134217705417,Split=[('s',)])
                        C(class=p,Purity=0.6358792184724689)
        I(Fidx=0,Score=0.024348496773761275,Split=[('c', 'k')])
                C(class=p,Purity=0.6993464052287581)
            I(Fidx=1,Score=0.04199857082741687,Split=[('g', 'y')])
                    C(class=p,Purity=1.0)
                I(Fidx=0,Score=0.0019084571122113259,Split=[('k',)])
                    C(class=p,Purity=0.8910505836575876)
    I(Fidx

In [159]:
pclasses=dt.predict(Xtest[:,feat])
#Lets see how good we are doing, by finding the accuracy on the test set..
print (np.sum(pclasses==Ytest))
print ("Accuracy = ", np.sum(pclasses==Ytest)/float(Ytest.shape[0]))

Prediction for single example:  ['k' 's']
Going to the right
Prediction for single example:  ['k' 's']
Going to the right
Prediction for single example:  ['k' 's']
Going to the right
Prediction for single example:  ['k' 's']
Going to the right
Prediction for single example:  ['k' 's']
Going to the right
Prediction for single example:  ['k' 's']
i am leaf label class: e
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
i am leaf label class: e
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction f

Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
i am leaf label class: e
Prediction for single example:  ['x' 'f']
Going to the right
Prediction for single example:  ['x' 'f']
Going to the right
Prediction for single example:  ['x' 'f']
Going to the right
Prediction for single example:  ['x' 'f']
Going to the right
Prediction for single example:  ['x' 'f']
Going to the right
Prediction for single example:  ['x' 'f']
i am leaf label class: e
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
i am leaf label class: e
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Predic

Prediction for single example:  ['x' 'f']
Going to the right
Prediction for single example:  ['x' 'f']
Going to the right
Prediction for single example:  ['x' 'f']
i am leaf label class: e
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
i am leaf label class: e
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
i am leaf label class: e
Prediction for single example:  ['f' 's']
Going to the right
Predic

In [139]:
from nose.tools import assert_greater_equal
Xtrain,Ytrain,Xtest,Ytest=t.split_data(X,Y)
feat=np.arange(2)
dt=DecisionTree(0.95,5,10)
dt.train(Xtrain[:,feat],Ytrain)


pclasses=dt.predict(Xtest[:,feat])
acc = np.sum(pclasses==Ytest)/float(Ytest.shape[0])

assert_greater_equal(acc, 0.60)

Prediction for single example:  ['f' 'f']
Going to the right
Prediction for single example:  ['f' 'f']
Going to the right
Prediction for single example:  ['f' 'f']
Going to the right
Prediction for single example:  ['f' 'f']
Going to the right
Prediction for single example:  ['f' 'f']
Going to the right
Prediction for single example:  ['f' 'f']
i am leaf label class: e
Prediction for single example:  ['x' 'f']
Going to the right
Prediction for single example:  ['x' 'f']
Going to the right
Prediction for single example:  ['x' 'f']
Going to the right
Prediction for single example:  ['x' 'f']
Going to the right
Prediction for single example:  ['x' 'f']
Going to the right
Prediction for single example:  ['x' 'f']
i am leaf label class: e
Prediction for single example:  ['f' 'f']
Going to the right
Prediction for single example:  ['f' 'f']
Going to the right
Prediction for single example:  ['f' 'f']
Going to the right
Prediction for single example:  ['f' 'f']
Going to the right
Prediction f

Prediction for single example:  ['f' 's']
Going to the right
Prediction for single example:  ['f' 's']
Going to the right
Prediction for single example:  ['f' 's']
Going to the right
Prediction for single example:  ['f' 's']
Going to the right
Prediction for single example:  ['f' 's']
Going to the right
Prediction for single example:  ['f' 's']
i am leaf label class: e
Prediction for single example:  ['f' 'f']
Going to the right
Prediction for single example:  ['f' 'f']
Going to the right
Prediction for single example:  ['f' 'f']
Going to the right
Prediction for single example:  ['f' 'f']
Going to the right
Prediction for single example:  ['f' 'f']
Going to the right
Prediction for single example:  ['f' 'f']
i am leaf label class: e
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction for single example:  ['x' 'y']
Going to the right
Prediction f

Prediction for single example:  ['f' 'f']
Going to the right
Prediction for single example:  ['f' 'f']
Going to the right
Prediction for single example:  ['f' 'f']
Going to the right
Prediction for single example:  ['f' 'f']
Going to the right
Prediction for single example:  ['f' 'f']
Going to the right
Prediction for single example:  ['f' 'f']
i am leaf label class: e
Prediction for single example:  ['x' 's']
Going to the right
Prediction for single example:  ['x' 's']
Going to the right
Prediction for single example:  ['x' 's']
Going to the right
Prediction for single example:  ['x' 's']
Going to the right
Prediction for single example:  ['x' 's']
Going to the right
Prediction for single example:  ['x' 's']
i am leaf label class: e
Prediction for single example:  ['k' 's']
Going to the right
Prediction for single example:  ['k' 's']
Going to the right
Prediction for single example:  ['k' 's']
Going to the right
Prediction for single example:  ['k' 's']
Going to the right
Prediction f

Prediction for single example:  ['x' 's']
Going to the right
Prediction for single example:  ['x' 's']
Going to the right
Prediction for single example:  ['x' 's']
Going to the right
Prediction for single example:  ['x' 's']
Going to the right
Prediction for single example:  ['x' 's']
i am leaf label class: e
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
i am leaf label class: e
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction for single example:  ['f' 'y']
Going to the right
Prediction f

AssertionError: 0.5178498153467378 not greater than or equal to 0.6

# Lets Train on all the features and for both the classes....

In [22]:
# Split your data into training and test-set... 
# see the documentation of split_data in tools for further information...
Xtrain,Ytrain,Xtest,Ytest=t.split_data(X,Y)

print (" Training Data Set Dimensions=", Xtrain.shape, "Training True Class labels dimensions", Ytrain.shape )  
print (" Test Data Set Dimensions=", Xtest.shape, "Test True Class labels dimensions", Ytrain.shape   )


 Training Data Set Dimensions= (5687, 22) Training True Class labels dimensions (5687,)
 Test Data Set Dimensions= (2437, 22) Test True Class labels dimensions (5687,)


In [23]:
feat=arange(22)#[0, 1, 2, 3]
dt=DecisionTree(0.95,5,10)
dt.train(Xtrain[:,feat],Ytrain)
pclasses=dt.predict(Xtest[:,feat])
#Lets see how good we are doing, by finding the accuracy on the test set..
print (np.sum(pclasses==Ytest))
print ("Accuracy = ", np.sum(pclasses==Ytest)/float(Ytest.shape[0]))

2398
Accuracy =  0.983996717275


In [24]:
print (dt)

---------------------------------------------------
 A Decision Tree With Depth=2
    C(class=p,Purity=1.0)
I(Fidx=4,Score=0.094673871403,Split=('a', 'l', 'n'))
    C(class=e,Purity=0.973240832507)
---------------------------------------------------


What can you conclude ?
====================
Please write your observation....



# Cross-Validation

Until now we have been splitting the dataset into a training and test set rather randomly and were reporting a rather artifical performance. Now we are going to test our system exhaustively by making use of k-fold [cross validation](http://en.wikipedia.org/wiki/Cross-validation_%28statistics%29). 

Now go and tune your hyper-parameters (purity, exthreshold) to opitmize the performance.

In [163]:
# Now lets cross validate for best paramters, and test the result...
# We will be training four different models on four different partitions of data set and 
# then will be reporting the mean accuracy of the four classifiers.

nfolds=4 # lets use four folds..
folds=t.generate_folds(X,Y,nfolds)
features=arange(22)#[0, 1, 2, 3] # features to use for our system
#now lets train and test on these folds...
totacc=[]
for k in range(nfolds):
    dt=DecisionTree(0.95,5,7)
    dt.train(folds[k][0][:,features],folds[k][1])
    pclasses=dt.predict(folds[k][2][:,features])
    acc=np.sum(pclasses==folds[k][3])/float(folds[k][3].shape[0])
    print (dt)
    print ("[Info] Fold {} Accuracy = {}".format(k+1, acc))
    totacc.append(acc)

print (totacc, '\n Mean Accuracy =', np.mean(totacc))

Generating CV data for 2 classes
Current purity of Y: 0.517971442639094
leaf node is not decided yet
Number of row: 6093
categoric is called
Best feature: 0
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Best feature: 3
Number of row: 6093
categoric is called
Best feature: 4
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of r

Prediction for single example:  ['f' 'y' 'g' 't' 'n' 'f' 'c' 'b' 'p' 't' 'b' 's' 's' 'p' 'p' 'p' 'w' 'o'
 'p' 'k' 'v' 'd']
Going to the right
Prediction for single example:  ['f' 'y' 'g' 't' 'n' 'f' 'c' 'b' 'p' 't' 'b' 's' 's' 'p' 'p' 'p' 'w' 'o'
 'p' 'k' 'v' 'd']
i am leaf label class: e
Prediction for single example:  ['f' 'f' 'n' 't' 'n' 'f' 'c' 'b' 'w' 't' 'b' 's' 's' 'g' 'g' 'p' 'w' 'o'
 'p' 'n' 'v' 'd']
Going to the right
Prediction for single example:  ['f' 'f' 'n' 't' 'n' 'f' 'c' 'b' 'w' 't' 'b' 's' 's' 'g' 'g' 'p' 'w' 'o'
 'p' 'n' 'v' 'd']
i am leaf label class: e
Prediction for single example:  ['f' 'f' 'e' 't' 'n' 'f' 'c' 'b' 'w' 't' 'b' 's' 's' 'w' 'p' 'p' 'w' 'o'
 'p' 'k' 'v' 'd']
Going to the right
Prediction for single example:  ['f' 'f' 'e' 't' 'n' 'f' 'c' 'b' 'w' 't' 'b' 's' 's' 'w' 'p' 'p' 'w' 'o'
 'p' 'k' 'v' 'd']
i am leaf label class: e
Prediction for single example:  ['x' 'y' 'g' 't' 'n' 'f' 'c' 'b' 'u' 't' 'b' 's' 's' 'w' 'w' 'p' 'w' 'o'
 'p' 'k' 'y' 'd']
Going t

Prediction for single example:  ['f' 'f' 'y' 'f' 'f' 'f' 'c' 'b' 'h' 'e' 'b' 'k' 'k' 'n' 'p' 'p' 'w' 'o'
 'l' 'h' 'v' 'g']
Going to the right
Prediction for single example:  ['f' 'f' 'y' 'f' 'f' 'f' 'c' 'b' 'h' 'e' 'b' 'k' 'k' 'n' 'p' 'p' 'w' 'o'
 'l' 'h' 'v' 'g']
i am leaf label class: e
Prediction for single example:  ['f' 'y' 'w' 't' 'n' 'f' 'c' 'b' 'g' 'e' 'b' 's' 's' 'w' 'w' 'p' 'w' 't'
 'p' 'r' 'v' 'm']
Going to the right
Prediction for single example:  ['f' 'y' 'w' 't' 'n' 'f' 'c' 'b' 'g' 'e' 'b' 's' 's' 'w' 'w' 'p' 'w' 't'
 'p' 'r' 'v' 'm']
i am leaf label class: e
Prediction for single example:  ['f' 'f' 'y' 'f' 'f' 'f' 'c' 'b' 'p' 'e' 'b' 'k' 'k' 'b' 'p' 'p' 'w' 'o'
 'l' 'h' 'y' 'p']
Going to the right
Prediction for single example:  ['f' 'f' 'y' 'f' 'f' 'f' 'c' 'b' 'p' 'e' 'b' 'k' 'k' 'b' 'p' 'p' 'w' 'o'
 'l' 'h' 'y' 'p']
i am leaf label class: e
Prediction for single example:  ['f' 's' 'n' 't' 'p' 'f' 'c' 'n' 'k' 'e' 'e' 's' 's' 'w' 'w' 'p' 'w' 'o'
 'p' 'k' 's' 'u']
Going t

Best feature: 0
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Best feature: 3
Number of row: 6093
categoric is called
Best feature: 4
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
The best root node is
 Best feature index: 4
 ('f', 'y', 'p', 'c', 's', 'm') 0.9016513328661303 

A node is bein

Prediction for single example:  ['b' 'f' 'y' 'f' 'n' 'f' 'c' 'n' 'w' 'e' '?' 'k' 'y' 'w' 'y' 'p' 'w' 'o'
 'e' 'w' 'v' 'd']
Going to the right
Prediction for single example:  ['b' 'f' 'y' 'f' 'n' 'f' 'c' 'n' 'w' 'e' '?' 'k' 'y' 'w' 'y' 'p' 'w' 'o'
 'e' 'w' 'v' 'd']
i am leaf label class: e
Prediction for single example:  ['x' 'y' 'g' 'f' 'f' 'f' 'c' 'b' 'p' 'e' 'b' 'k' 'k' 'p' 'b' 'p' 'w' 'o'
 'l' 'h' 'y' 'g']
Going to the right
Prediction for single example:  ['x' 'y' 'g' 'f' 'f' 'f' 'c' 'b' 'p' 'e' 'b' 'k' 'k' 'p' 'b' 'p' 'w' 'o'
 'l' 'h' 'y' 'g']
i am leaf label class: e
Prediction for single example:  ['x' 's' 'n' 'f' 'y' 'f' 'c' 'n' 'b' 't' '?' 'k' 's' 'p' 'w' 'p' 'w' 'o'
 'e' 'w' 'v' 'l']
Going to the right
Prediction for single example:  ['x' 's' 'n' 'f' 'y' 'f' 'c' 'n' 'b' 't' '?' 'k' 's' 'p' 'w' 'p' 'w' 'o'
 'e' 'w' 'v' 'l']
i am leaf label class: e
Prediction for single example:  ['x' 'y' 'w' 't' 'p' 'f' 'c' 'n' 'w' 'e' 'e' 's' 's' 'w' 'w' 'p' 'w' 'o'
 'p' 'k' 's' 'u']
Going t

Best feature: 0
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Best feature: 3
Number of row: 6093
categoric is called
Best feature: 4
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
The best root node is
 Best feature index: 4
 ('f', 'y', 'p', 'c', 's', 'm') 0.8974380126101213 

A node is bein

Prediction for single example:  ['f' 'y' 'g' 'f' 'f' 'f' 'c' 'b' 'g' 'e' 'b' 'k' 'k' 'n' 'n' 'p' 'w' 'o'
 'l' 'h' 'y' 'd']
i am leaf label class: e
Prediction for single example:  ['f' 'y' 'e' 'f' 'y' 'f' 'c' 'n' 'b' 't' '?' 's' 'k' 'w' 'w' 'p' 'w' 'o'
 'e' 'w' 'v' 'd']
Going to the right
Prediction for single example:  ['f' 'y' 'e' 'f' 'y' 'f' 'c' 'n' 'b' 't' '?' 's' 'k' 'w' 'w' 'p' 'w' 'o'
 'e' 'w' 'v' 'd']
i am leaf label class: e
Prediction for single example:  ['x' 'f' 'w' 'f' 'c' 'f' 'w' 'n' 'n' 'e' 'b' 's' 's' 'w' 'w' 'p' 'w' 'o'
 'p' 'k' 's' 'd']
Going to the right
Prediction for single example:  ['x' 'f' 'w' 'f' 'c' 'f' 'w' 'n' 'n' 'e' 'b' 's' 's' 'w' 'w' 'p' 'w' 'o'
 'p' 'k' 's' 'd']
i am leaf label class: e
Prediction for single example:  ['f' 'f' 'y' 'f' 'f' 'f' 'c' 'b' 'g' 'e' 'b' 'k' 'k' 'n' 'b' 'p' 'w' 'o'
 'l' 'h' 'y' 'g']
Going to the right
Prediction for single example:  ['f' 'f' 'y' 'f' 'f' 'f' 'c' 'b' 'g' 'e' 'b' 'k' 'k' 'n' 'b' 'p' 'w' 'o'
 'l' 'h' 'y' 'g']
i am le

Best feature: 0
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Best feature: 3
Number of row: 6093
categoric is called
Best feature: 4
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
Number of row: 6093
categoric is called
The best root node is
 Best feature index: 4
 ('f', 'y', 'p', 'c', 's', 'm') 0.9025015571829461 

A node is bein

Prediction for single example:  ['s' 'f' 'n' 'f' 'n' 'f' 'c' 'n' 'g' 'e' 'e' 's' 's' 'w' 'w' 'p' 'w' 'o'
 'p' 'k' 'y' 'u']
i am leaf label class: e
Prediction for single example:  ['x' 'f' 'n' 't' 'n' 'f' 'c' 'b' 'p' 't' 'b' 's' 's' 'p' 'g' 'p' 'w' 'o'
 'p' 'n' 'v' 'd']
Going to the right
Prediction for single example:  ['x' 'f' 'n' 't' 'n' 'f' 'c' 'b' 'p' 't' 'b' 's' 's' 'p' 'g' 'p' 'w' 'o'
 'p' 'n' 'v' 'd']
i am leaf label class: e
Prediction for single example:  ['x' 'y' 'y' 't' 'l' 'f' 'c' 'b' 'g' 'e' 'c' 's' 's' 'w' 'w' 'p' 'w' 'o'
 'p' 'n' 'n' 'm']
Going to the right
Prediction for single example:  ['x' 'y' 'y' 't' 'l' 'f' 'c' 'b' 'g' 'e' 'c' 's' 's' 'w' 'w' 'p' 'w' 'o'
 'p' 'n' 'n' 'm']
i am leaf label class: e
Prediction for single example:  ['x' 'f' 'e' 't' 'n' 'f' 'c' 'b' 'p' 't' 'b' 's' 's' 'p' 'w' 'p' 'w' 'o'
 'p' 'k' 'y' 'd']
Going to the right
Prediction for single example:  ['x' 'f' 'e' 't' 'n' 'f' 'c' 'b' 'p' 't' 'b' 's' 's' 'p' 'w' 'p' 'w' 'o'
 'p' 'k' 'y' 'd']
i am le

Prediction for single example:  ['x' 'y' 'e' 'f' 'f' 'f' 'c' 'n' 'b' 't' '?' 'k' 's' 'p' 'w' 'p' 'w' 'o'
 'e' 'w' 'v' 'd']
i am leaf label class: e
Prediction for single example:  ['f' 's' 'e' 'f' 's' 'f' 'c' 'n' 'b' 't' '?' 'k' 's' 'w' 'w' 'p' 'w' 'o'
 'e' 'w' 'v' 'd']
Going to the right
Prediction for single example:  ['f' 's' 'e' 'f' 's' 'f' 'c' 'n' 'b' 't' '?' 'k' 's' 'w' 'w' 'p' 'w' 'o'
 'e' 'w' 'v' 'd']
i am leaf label class: e
Prediction for single example:  ['k' 's' 'n' 'f' 's' 'f' 'c' 'n' 'b' 't' '?' 'k' 's' 'p' 'p' 'p' 'w' 'o'
 'e' 'w' 'v' 'p']
Going to the right
Prediction for single example:  ['k' 's' 'n' 'f' 's' 'f' 'c' 'n' 'b' 't' '?' 'k' 's' 'p' 'p' 'p' 'w' 'o'
 'e' 'w' 'v' 'p']
i am leaf label class: e
Prediction for single example:  ['f' 'y' 'e' 'f' 'm' 'f' 'c' 'b' 'w' 'e' 'c' 'k' 'y' 'c' 'c' 'p' 'w' 'n'
 'n' 'w' 'c' 'd']
Going to the right
Prediction for single example:  ['f' 'y' 'e' 'f' 'm' 'f' 'c' 'b' 'w' 'e' 'c' 'k' 'y' 'c' 'c' 'p' 'w' 'n'
 'n' 'w' 'c' 'd']
i am le

In [26]:
# Now lets cross validate for best paramters, and test the result...
# We will be training four different models on four different partitions of data set and 
# then will be reporting the mean accuracy of the four classifiers.

nfolds=4 # lets use four folds..
folds=t.generate_folds(X,Y,nfolds)
features=[0,1, 2, 3] # features to use for our system
#now lets train and test on these folds...

#Lets perform the grid search...
purity=np.linspace(0.85,0.97,13)
nexamp=np.linspace(5,25,21)  

params=np.zeros((len(purity),len(nexamp)))
                   
for p in range(len(purity)):
    for n in range(len(nexamp)):
        totacc=[]
        for k in range(nfolds):
            dt=DecisionTree(purity[p],nexamp[n],7)#purity[p],nexamp[n])
            dt.train(folds[k][0][:,features],folds[k][1])
            pclasses=dt.predict(folds[k][2][:,features])
            acc=np.sum(pclasses==folds[k][3])/float(folds[k][3].shape[0])
            print ("[Info] Fold {} Accuracy = {}".format(k+1, acc))
            totacc.append(acc)
        params[p,n]=np.mean(totacc)
        print (totacc, '\nPurity={}, Nexample-threshold={}, Mean Accuracy ={}'.format(purity[p],nexamp[n], np.mean(totacc)))

Generating CV data for 2 classes
[Info] Fold 1 Accuracy = 0.859182668636
[Info] Fold 2 Accuracy = 0.841457410143
[Info] Fold 3 Accuracy = 0.844903988183
[Info] Fold 4 Accuracy = 0.829148202856
[0.85918266863613979, 0.84145741014278685, 0.84490398818316104, 0.82914820285573609] 
Purity=0.85, Nexample-threshold=5.0, Mean Accuracy =0.843673067454
[Info] Fold 1 Accuracy = 0.859182668636
[Info] Fold 2 Accuracy = 0.841457410143
[Info] Fold 3 Accuracy = 0.844903988183
[Info] Fold 4 Accuracy = 0.829148202856
[0.85918266863613979, 0.84145741014278685, 0.84490398818316104, 0.82914820285573609] 
Purity=0.85, Nexample-threshold=6.0, Mean Accuracy =0.843673067454
[Info] Fold 1 Accuracy = 0.859182668636
[Info] Fold 2 Accuracy = 0.841457410143
[Info] Fold 3 Accuracy = 0.844903988183
[Info] Fold 4 Accuracy = 0.829148202856
[0.85918266863613979, 0.84145741014278685, 0.84490398818316104, 0.82914820285573609] 
Purity=0.85, Nexample-threshold=7.0, Mean Accuracy =0.843673067454
[Info] Fold 1 Accuracy = 0.8

In [28]:
np.unravel_index(np.argmax(params), params.shape)

(12, 0)